In [3]:
"""
BP Test
"""
import numpy as np
import math
import matplotlib.pyplot as plt

#sigmoid function and its diff
def sigmoid(x):
    return 1.0 / (1 + np.exp(-x))

def diff_sigmoid(x):
    fval = sigmoid(x)
    return fval * (1 - fval)

class BP:
    def __init__(self, n_hidden=None, f_hidden='sigmoid', f_output='sigmoid',
                 epsilon=1e-3, maxstep=1000, eta=0.1, alpha=0.0): 
        self.n_input = None  # input layer cell number
        self.n_hidden = n_hidden  # hidden layer cell number
        self.n_output = None
        self.f_hidden = f_hidden
        self.f_output = f_output
        self.epsilon = epsilon
        self.maxstep = maxstep
        self.eta = eta  #  learning rate
        self.alpha = alpha  # factor

        self.wih = None  # input layer to hidden layer weight matrix
        self.who = None  # hidden layer to output layer weight matrix
        self.bih = None  # input layer to hidden layer bias
        self.bho = None  # hidden layer to output layer bias
        self.N = None

        return None
    
    def init_param(self, X_data, y_data):
        if len(X_data.shape) == 1:  # if input is one-dimension, transpose to be N dimension.
            X_data = np.transpose([X_data])
        self.N = X_data.shape[0]
        if len(y_data.shape) == 1:
            y_data = np.transpose([y_data])
        self.n_input = X_data.shape[1]
        self.n_output = y_data.shape[1]
        if self.n_hidden is None:
            self.n_hidden = int(math.ceil(math.sqrt(self.n_input + self.n_output)) + 2)
        self.wih = np.random.rand(self.n_input, self.n_hidden)  # i*h
        self.who = np.random.rand(self.n_hidden, self.n_output)  # h*o
        self.bih = np.random.rand(self.n_hidden)  # h
        self.bho = np.random.rand(self.n_output)  # o
        return X_data, y_data
    
    def forward(self, X_data):
        # forward 
        x_hidden_in = X_data @ self.wih + self.bih  # n*h
        x_hidden_out = sigmoid(x_hidden_in)  # n*h
        x_output_in = x_hidden_out @ self.who + self.bho  # n*o
        x_output_out = sigmoid(x_output_in)  # n*o
        return x_output_out, x_output_in, x_hidden_out, x_hidden_in

    def fit(self, X_data, y_data):
        X_data, y_data = self.init_param(X_data, y_data)
        step = 0
        # Initialize all deltas
        delta_wih = np.zeros_like(self.wih)
        delta_who = np.zeros_like(self.who)
        delta_bih = np.zeros_like(self.bih)
        delta_bho = np.zeros_like(self.bho)
        while step < self.maxstep:
            step += 1
            # forward 
            x_output_out, x_output_in, x_hidden_out, x_hidden_in = self.forward(X_data)
            if np.sum(abs(x_output_out - y_data)) < self.epsilon:
                break
                
            # loss back pro
            err_output = y_data - x_output_out           # n*o， ouput layer, every cell's error
            print("step {} error_output {} ".format(step, err_output))
            delta_ho = -err_output * diff_sigmoid(x_output_in)  # n*o
            err_hidden = delta_ho @ self.who.T  # n*h， 隐藏层（相当于输入层的输出），每个神经元上的误差
           
            # 隐藏层到输出层权值及阈值更新
            delta_bho = np.sum(self.eta * delta_ho + self.alpha * delta_bho, axis=0) / self.N
            self.bho -= delta_bho
            
            delta_who = self.eta * x_hidden_out.T @ delta_ho + self.alpha * delta_who
            self.who -= delta_who
            
            # 输入层到隐藏层权值及阈值的更新
            delta_ih = err_hidden * diff_sigmoid(x_hidden_in)  # n*h
            delta_bih = np.sum(self.eta * delta_ih + self.alpha * delta_bih, axis=0) / self.N
            self.bih -= delta_bih
            
            delta_wih = self.eta * X_data.T @ delta_ih + self.alpha * delta_wih
            self.wih -= delta_wih
        return None

    def predict(self, X):
        # 预测
        res = self.forward(X)
        return res[0]
    
if __name__ == '__main__':

    N = 100
    X_data = np.linspace(-1, 1, N)
    X_data = np.transpose([X_data])
    y_data = np.exp(-X_data) * np.sin(2 * X_data)
    bp = BP(f_output='linear', maxstep=2000, eta=0.01, alpha=0.1)  # 注意学习率若过大，将导致不能收敛
    bp.fit(X_data, y_data)
    plt.plot(X_data, y_data)
    pred = bp.predict(X_data)
    plt.scatter(X_data, pred, color='r')
    plt.show()

step 1 error_output [[-3.14747681]
 [-3.14125705]
 [-3.13036997]
 [-3.11502295]
 [-3.09542406]
 [-3.07178162]
 [-3.04430382]
 [-3.01319824]
 [-2.9786715 ]
 [-2.9409289 ]
 [-2.900174  ]
 [-2.85660836]
 [-2.81043114]
 [-2.76183886]
 [-2.71102509]
 [-2.65818014]
 [-2.60349088]
 [-2.54714044]
 [-2.48930805]
 [-2.43016876]
 [-2.36989333]
 [-2.30864803]
 [-2.24659447]
 [-2.18388947]
 [-2.12068496]
 [-2.05712783]
 [-1.99335987]
 [-1.92951768]
 [-1.86573257]
 [-1.80213056]
 [-1.7388323 ]
 [-1.67595306]
 [-1.6136027 ]
 [-1.55188567]
 [-1.49090102]
 [-1.4307424 ]
 [-1.37149811]
 [-1.31325111]
 [-1.2560791 ]
 [-1.20005452]
 [-1.14524468]
 [-1.09171176]
 [-1.03951295]
 [-0.98870048]
 [-0.93932177]
 [-0.89141945]
 [-0.84503154]
 [-0.80019152]
 [-0.75692844]
 [-0.71526703]
 [-0.67522787]
 [-0.63682745]
 [-0.60007834]
 [-0.5649893 ]
 [-0.53156543]
 [-0.49980829]
 [-0.46971605]
 [-0.44128361]
 [-0.41450276]
 [-0.38936231]
 [-0.36584823]
 [-0.34394377]
 [-0.32362967]
 [-0.30488419]
 [-0.28768336]
 [-0.